In [55]:
import pandas as pd
from collections import Counter
import re
import os
import warnings
import sys
import numpy as np
warnings.simplefilter('ignore')
sys.path.append("/2_findflags/all_subreddits")

In [56]:
del sys.modules['functions_pos']

In [57]:
import functions_pos as pos

In [26]:
from IPython.core.display import display, HTML

def highlight_re(text, regex):
    htmld = re.sub(r'('+regex+')', '<mark>' + r'\1' + '</mark>', text.lower())
    display(HTML(htmld))
    
def print_submission(i, index, row):
    print('\n\n\nr/%s \n--------------------' % (index[0]))
    print('Published: %s' % row.subm_created[:20])
    print('%d | SUBM: %10s | COMM: %10s\n--------------------' % (i, index[1], index[2]))
    highlight_re('<b>'+row.subm_title+'</b>', covid_regex)
    print('URL: %s\nSubmission score: %d' % (row.subm_url, row.subm_score))

def print_comment(i, index, row, flag_no, limit = 1000):
    print('\nFLAG #%d (score = %d)' % (flag_no, row.comm_score))
    highlight_re(row.comm_body[:limit], fake_regex)    
    
def ftab(series, rnd = 3):
    return pd.concat([series.value_counts(),series.value_counts(normalize = True).round(rnd)],axis =1)

In [7]:
united_file = sorted([filename for filename in os.listdir('../../output/') if re.search('UNITED_[0-9][0-9].+csv',filename)])[-1]
united_file

'UNITED_2020-05-01.csv'

In [9]:
COMSBSR = pd.read_csv('../../output/'+united_file).\
    assign(comm_direct = lambda df: df['comm_parent_id'].str.contains('t3_')).\
    set_index(['subreddit','subm_id','comm_id']).\
    sort_values('subm_created', ascending = False)
COMSBSR['comm_body'] = COMSBSR['comm_body'].astype(str)
COMSBSR.shape

(4125744, 20)

In [10]:
COMSBSR.to_csv('../../output/'+united_file+"_SRT")

In [39]:
ftab(COMSBSR.comm_direct)

comm_direct  comm_direct
True       2432359         0.59
False      1693385         0.41

In [32]:
covid_regex = '|'.join(pd.read_csv('../../input/keywords_covid.txt',header=None).loc[:,0].\
                  str.replace("\\(|\\)",r"").str.replace(r"\*",r""))#r"\\w*"))
fake_regex = '(fake |false).{0,15}(new\\w|info\\w|hood\\w)'+'|'+\
             '(dis|mis|mal)(info\\w|leading)'+'|'+\
             '\\bbs\\b|\\bbullshit\\b'+\
             '(not ).{0,5}(true\\b|verif\\w|real\\b)'+'|'+\
             '(unreli\\w+|unverifi\\w+|untrustw\\w+|fake\\w+)( source)'
fake_regex_no = '((no|not) .{0,10}('+fake_regex+'))'+'|(users often report submissions from this site)'

In [44]:
highlight_re('some americans are misinformed about the coronavirus. how responsible is the media?', fake_regex)

In [34]:
COMM_WITH_FLAGS = COMSBSR.\
    query('comm_body.str.contains("'+fake_regex+'")').\
    query('not comm_body.str.contains("'+fake_regex_no+'")').\
    query('not subm_title.str.contains("'+fake_regex+'")').\
    query('comm_direct')
COMM_WITH_FLAGS.shape

(18064, 20)

## Extract comments with POS

In [75]:
fake_regex_partatt

'sensationalized|manipulative|misleading|bs|propaganda|unverified|clickbait|fabricated|editorialized|manipulated|fake|false|bogus|unreliable|bullshit|untrustworthy'

In [84]:
fake_regex_fullobj

'\\binnacuracies|\\bmisleading|\\bbs|\\bmisinformation|\\bpropaganda|\\bunverified|\\bclickbait|\\bmalinformation|\\bfabrication|\\bfalsehood|\\bunreliable|\\bdisinformation|\\bbullshit|\\buntrustworthy'

In [83]:
fake_regex_fullobj = '|'.join([r'\b'+w for w in pos.all_keywords['fullobjects']])
fake_regex_partobj = '|'.join([r'\b'+w for w in pos.all_keywords['partialobjects']])
fake_regex_partatt = '|'.join([r'\b'+w for w in pos.all_keywords['attributes']])

In [90]:
pd.DataFrame({'b': TEMP.comm_body[10:20],
              'fo': TEMP.comm_body[10:20].str.contains(fake_regex_fullobj),
              'po': TEMP.comm_body[10:20].str.contains(fake_regex_partobj),
              'pa': TEMP.comm_body[10:20].str.contains(fake_regex_partatt)}).\
    assign(total = lambda df: df.fo | (df.po & df.pa))

b     fo     po  \
100370  Images, video, podcast, gif, and other types o...  False   True   
100401  The study is about administering 3x the normal...   True   True   
100516  Hello everyone, we would just like to remind a...   True   True   
100556  **Step 1** A new virus starts to spread around...  False   True   
100592  Hello everyone, we would just like to remind a...   True   True   
100596  This submission appears to related to the deve...   True   True   
100610  The photo in the thumbnail is misleading. I be...   True  False   
100626  Due to the nature of this topic, users spreadi...   True   True   
100636            Oh he must be subscribed to r/askreddit  False   True   
100661  It is very weird if true. I think we should be...   True  False   

           pa  total  
100370  False  False  
100401   True   True  
100516  False   True  
100556  False  False  
100592  False   True  
100596   True   True  
100610   True   True  
100626  False   True  
100636  False  False  
100661   True   True

In [95]:
united_file = sorted([filename for filename in os.listdir('../../output/') if re.search('UNITED_[0-9][0-9].+csv',filename)])[-1]
READR = pd.read_csv('../../output/'+united_file, chunksize=100000)

In [96]:
HASREGEX = pd.DataFrame()
n = 0
for TOP in READR:
    TEMP = TOP[(TOP.comm_body.str.contains(fake_regex_fullobj)) | \
               (TOP.comm_body.str.contains(fake_regex_partobj)) | \
               (TOP.comm_body.str.contains(fake_regex_partatt)) ]
    n+=TOP.shape[0]
    HASREGEX = HASREGEX.append(TEMP, ignore_index = True)
    print('Found %7d / %10d' % (HASREGEX.shape[0], n))

Found   14057 /     100000
Found   27696 /     200000
Found   41457 /     300000
Found   55697 /     400000
Found   69513 /     500000
Found   83899 /     600000
Found   98919 /     700000
Found  113192 /     800000
Found  127193 /     900000
Found  142018 /    1000000
Found  155732 /    1100000
Found  169545 /    1200000
Found  183127 /    1300000
Found  196615 /    1400000
Found  209655 /    1500000
Found  222347 /    1600000
Found  235175 /    1700000
Found  248641 /    1800000
Found  261568 /    1900000
Found  274672 /    2000000
Found  287656 /    2100000
Found  299853 /    2200000
Found  313182 /    2300000
Found  325187 /    2400000
Found  336829 /    2500000
Found  350956 /    2600000
Found  364899 /    2700000
Found  379036 /    2800000
Found  392880 /    2900000
Found  406709 /    3000000
Found  420923 /    3100000
Found  434803 /    3200000
Found  449559 /    3300000
Found  464228 /    3400000
Found  478491 /    3500000
Found  492520 /    3600000
Found  507162 /    3700000
F

In [98]:
HASREGEXSH = HASREGEX[\
               (HASREGEX.comm_body.str.contains(fake_regex_fullobj)) | \
               ((HASREGEX.comm_body.str.contains(fake_regex_partobj)) & \
                (HASREGEX.comm_body.str.contains(fake_regex_partatt))) ]
HASREGEXSH.shape

(122866, 23)

In [99]:
HASREGEXSH.to_csv('../../output/HASREGEXSH.csv')

In [97]:
HASREGEX.to_csv('../../output/HASREGEX.csv')

In [17]:
fake_regex_pos = '|'.join(list({x for values in pos.all_keywords.values() for x in values}.difference(set(['it','be']))))
fake_regex_pos

'bullshit|spread|unreliable|make|header|unverified|bs|misleading|info|sound|fabrication|article|come|propaganda|seem|bogus|stop|you|website|this|feel|clickbait|misinformation|information|manipulative|fake|untrustworthy|false|source|smell|propagate|title|editorialized|news|look|url|link|post|falsehood|headline|distribute|produce|disinformation|manipulated'

In [30]:
fake_regex_fullobj

'misleading|misinformation|propaganda|unverified|clickbait|malinformation|fabrication|falsehood|unreliable|disinformation|untrustworthy'

subreddit    subm_id     comm_id  \
1      conspiracy  t3_g96qmm  t1_form19c   
7      POTUSWatch  t3_g96p67  t1_forj6dy   
8      POTUSWatch  t3_g96oya  t1_forj4x5   
106   Coronavirus  t3_g96l4a  t1_forj215   
187   Coronavirus  t3_g96l0w  t1_forio46   
...           ...        ...         ...   
9485     politics  t3_g937om  t1_for8znz   
9766      COVID19  t3_g936ij  t1_for573d   
9854  Coronavirus  t3_g935yt  t1_for0w42   
9947  Coronavirus  t3_g933xl  t1_foqxec5   
9987     politics  t3_g9338s  t1_foqzeim   

                                              comm_body         comm_created  \
1     Your post has been removed because it does not...  2020-04-27 19:08:26   
7     Remember, be friendly! Attack the argument, no...  2020-04-27 18:45:28   
8     Remember, be friendly! Attack the argument, no...  2020-04-27 18:45:09   
106   Your submission has been removed because * **P...  2020-04-27 18:44:30   
187   In an attempt to prove they haven’t been sprea...  2020-04-27 18:41:26   
...                                                 ...                  ...   
9485  There has to be some way Trump can be fucked b...  2020-04-27 17:23:31   
9766  &gt; Next we report on **three compounds not c...  2020-04-27 16:52:50   
9854  I’ve been keeping up with this article since i...  2020-04-27 16:17:26   
9947  There’s literally no evidence showing that peo...  2020-04-27 15:48:23   
9987  &gt;Why, when 200,000 have died around the wor...  2020-04-27 16:05:02   

     comm_parent_id          comm_author  comm_score  comm_collapsed  \
1         t3_g96qmm              rConBot         1.0           False   
7         t3_g96p67  POTUS_Archivist_Bot         1.0           False   
8         t3_g96oya  POTUS_Archivist_Bot         1.0           False   
106       t3_g96l4a          dreamweavur         1.0           False   
187       t3_g96l0w            Swiftlass         6.0           False   
...             ...                  ...         ...             ...   
9485      t3_g937om             strugglz         1.0           False   
9766      t3_g936ij     proudbakunkinman         3.0           False   
9854      t3_g935yt          TxCoolGuy29         0.0           False   
9947      t3_g933xl  arise_chickin_arise         1.0           False   
9987      t3_g9338s     BeheldaPaleHorse         1.0           False   

     comm_author_class  ...     subm_domain          subm_author subm_score  \
1            moderator  ...        shrm.org          ihavetopoop        0.0   
7            moderator  ...     foxnews.com  POTUS_Archivist_Bot        1.0   
8            moderator  ...     foxnews.com  POTUS_Archivist_Bot        1.0   
106          moderator  ...     thehill.com              djhimeh        5.0   
187               user  ...        cnbc.com            FredoSosa        0.0   
...                ...  ...             ...                  ...        ...   
9485              user  ...    huffpost.com           growyurown       67.0   
9766              user  ...     biorxiv.org           FreshLine_        6.0   
9854              user  ...  nbcnewyork.com         BrooklynRU39       26.0   
9947              user  ...        cnbc.com            [deleted]        1.0   
9987              user  ...     nbcnews.com     WhileFalseRepeat       58.0   

     subm_ncomm                                         subm_flair  \
1          13.0                                                NaN   
7           2.0                                            Article   
8           2.0                                            Article   
106        10.0  Removed - Off-topic political discussion Remov...   
187        30.0                            Central &amp; East Asia   
...         ...                                                ...   
9485       21.0                                                NaN   
9766        9.0                                           Preprint   
9854      255.0                                                USA   
9947

In [29]:
TOP.query(query_regex, engine='python')

UndefinedVariableError: name 'fake_regex_fullobj' is not defined

### Printing

In [90]:
def print_comm(DF):
    old_url, old_comm = 'blank','blank'
    iter_com, iter_found = 1,1
    for row in DF[DF['comm_direct']].itertuples():
        txt = row.comm_body
        url = row.subm_url
        if len(txt)<1000:
            for sent in pos.get_sent(txt):
                fp = sent._.fake_news_flag
                if fp:
                    #Print for each submission
                    if url!=old_url:
                        print('\n')
                        display(HTML('<i>r/'+ row.subreddit+'</i>'))
                        print(row.subm_url)
                        print(row.subm_title)
                        print(row.subm_created)
                        print('%4d / %6d' % (iter_found, iter_com))
                        old_url = url
                    #Print for each comment
                    if old_comm != txt:
                        highlight_re('<p>->: ' + txt + '</p>', fake_regex_pos)
                        old_comm = txt
                        iter_found+=1
                    #Print for each sentence
                    display(HTML('<p><b>'+fp+'</b></p>'))
    iter_com+=1

In [91]:
print_comm(TOP)

https://www.breitbart.com/health/2020/04/02/patrick-courrielche-media-helped-democrats-ignore-coronavirus-by-hyping-impeachment/
Patrick Courrielche: Media Helped Democrats Ignore Coronavirus by Hyping Imp
2020-04-03 02:48:56
   1 /      1


https://www.cnn.com/world/live-news/coronavirus-pandemic-04-02-20-intl/h_7928afb03efd8f4c7c7e3299663712a4
Top US infectious diseases expert calls for a federally mandated stay-at-home order
2020-04-03 02:43:08
   2 /      1


https://nymag.com/intelligencer/2020/04/read-trumps-letter-blaming-coronavirus-in-ny-on-impeachment.html
Read Trump’s Letter to Chuck Schumer Blaming Coronavirus in New York on Impeachment
2020-04-03 02:42:49
   3 /      1


https://www.detroitnews.com/story/news/local/detroit-city/2020/04/02/ddot-driver-who-said-woman-coughed-his-bus-dies/5111053002/
DDOT driver who said woman coughed on his bus dies of COVID-19
2020-04-03 02:35:24
   4 /      1


https://publicintegrity.org/health/coronavirus-and-inequality/the-labor-department-wont-take-steps-to-protect-health-care-workers-from-the-coronavirus/
The Labor Department won’t take steps to protect health care workers from the coronavirus – The U.S. Department of Labor has rejected pressure to issue worker protections that nurses are demanding. The hospital industry wants it that way.
2020-04-03 02:27:38
   5 /      1


...

https://metro.co.uk/2020/03/27/people-syndrome-may-lower-priority-live-saving-coronavirus-care-12466194/
People with Down syndrome could be left to die of coronavirus to ‘save’ medical supplies
2020-03-28 13:39:39
1210 /      1


https://www.nhregister.com/news/coronavirus/article/Mayor-New-Haven-asks-for-coronavirus-help-Yale-15162606.php
Mayor: New Haven asks for coronavirus housing help; Yale says ‘no’
2020-03-28 13:33:01
1211 /      1


https://www.abcactionnews.com/news/local-news/i-team-investigates/data-shows-amazon-raised-prices-during-pandemic-alongside-sellers-accused-of-price-gouging
Data shows Amazon raised prices during pandemic alongside sellers accused of price gouging
2020-03-28 13:22:45
1212 /      1


https://www.wired.com/story/google-bans-infowars-android-app-alex-jones-coronavirus/
Google Bans Infowars Android App Over Coronavirus Claims: Apple kicked Alex Jones out of the App Store in 2018. The Google Play Store has finally followed suit.
2020-03-28 13:21:21
1217 /      1


https://www.esquire.com/news-politics/politics/a31960091/ventilators-are-expensive-until-you-remember-the-f-35/
Ventilators Are Expensive Until You Remember the F-35
2020-03-28 13:14:45
1219 /      1


In [34]:
old_url, old_comm = 'blank','blank'
iter_com, iter_found = 1,1
for row in TOP[TOP['comm_direct']].itertuples():
    txt = row.comm_body
    url = row.subm_url
    if len(txt)<1000:
        for sent in pos.get_sent(txt):
            fp = sent._.fake_news_flag
            if fp:
                if url!=old_url:
                    print('\n')
                    display(HTML('<i>r/'+ row.subreddit+'</i>'))
                    print(url)
                    print(row.subm_created)
                    print('%4d / %6d' % (iter_found, iter_com))
                    old_url = url
                if old_comm != txt:
                    highlight_re('<p>->: ' + txt + '</p>', fake_regex_pos)
                    old_comm = txt
                    iter_found+=1
                display(HTML('<p><b>'+fp+'</b></p>'))
    iter_com+=1        

https://www.cbsnews.com/news/weekly-jobless-claims-report-unemployment-6-6-million/
2020-04-09 18:35:04
   1 /    138


https://www.dailysabah.com/politics/desperate-for-medical-supplies-us-asks-to-buy-from-turkey/news
2020-04-09 18:16:33
   2 /    627


https://kprcradio.iheart.com/featured/walton-and-johnson/content/2020-04-09-registered-nurse-ill-deny-trump-supporter-coronavirus-treatment/
2020-04-09 18:11:12
   3 /    876


https://www.vox.com/2020/4/9/21210353/coronavirus-health-insurance-biden-sanders-medicare-for-all
2020-04-09 18:10:28
   4 /    899


https://bgr.com/2020/04/09/coronavirus-outdoors-exercise-social-distancing/
2020-04-09 18:09:23
   5 /    932


...

https://news.sky.com/story/coronavirus-number-of-daily-covid-19-deaths-in-spain-continues-to-fall-11968826
2020-04-05 13:40:20
 867 / 187695


https://www.alternet.org/2020/03/how-trumps-mental-unfitness-raises-a-fraught-dilemma-for-dealing-with-him-in-a-crisis/
2020-04-05 13:37:51
 868 / 187748


https://news.sky.com/story/coronavirus-number-of-daily-covid-19-deaths-in-spain-continues-to-fall-11968826
2020-04-05 13:36:38
 869 / 187791


https://www.theguardian.com/world/2020/apr/05/face-mask-protect-coronavirus-covid-19-myths-busted?utm_term=Autofeed&amp;CMP=twt_gu&amp;utm_medium&amp;utm_source=Twitter#Echobox=1586077527
2020-04-05 13:12:34
 870 / 188201


TypeError: object of type 'float' has no len()

In [36]:
870/188201

0.00462271720129011

In [92]:
sent_lst = []
for row in TOP[TOP['comm_direct']].itertuples():
    if len(row.comm_body)<1000:
        for sent in pos.get_sent(row.comm_body):
            sent_lst.append((row.comm_id, sent.text, sent._.fake_news_flag))

In [93]:
sent_df = pd.DataFrame(sent_lst, columns = ['comm_id','sent','fake_news_flag'])
sent_df['comm_has_flags'] = sent_df.groupby('comm_id')['fake_news_flag'].transform('count')
sent_df['sent_id'] = sent_df.groupby('comm_id').cumcount() + 1
sent_df.set_index(['comm_id','sent_id'], inplace = True)
sent_df['fake_regex'] =np.logical_or(\
                        sent_df['sent'].str.contains(fake_regex_fullobj),
                        np.logical_and(sent_df['sent'].str.contains(fake_regex_partobj),
                                       sent_df['sent'].str.contains(fake_regex_partatt)))

sent  \
comm_id    sent_id                                                      
t1_fm9xko2 1        [https://giphy.com/gifs/pDsCoECKh1Pa](https://...   
t1_fm9xn5t 1                                    May they rest in hell   
t1_fm9xwr3 1                   Well, well, well, how the turn tables.   
t1_fm9xzo3 1                                                [removed]   
t1_fm9y524 1                                                [removed]   
...                                                               ...   
t1_flqkoxy 5                           Trump is simple a poor leader.   
t1_flqkhgb 1                 He is a narcissist of the highest order.   
           2                         He must be removed from office .   
t1_flqk0lf 1                            Sic semper tyrannis: carcerem   
t1_flqjdf1 1        The only way to cure a teenage bully is to lov...   

                   fake_news_flag  comm_has_flags  
comm_id    sent_id                                 
t1_fm9xko2 1                 None               0  
t1_fm9xn5t 1                 None               0  
t1_fm9xwr3 1                 None               0  
t1_fm9xzo3 1                 None               0  
t1_fm9y524 1                 None               0  
...                           ...             ...  
t1_flqkoxy 5                 None               0  
t1_flqkhgb 1                 None               0  
           2                 None               0  
t1_flqk0lf 1                 None               0  
t1_flqjdf1 1                 None               0  

[784581 rows x 3 columns]

In [138]:
sent_df

sent  \
comm_id    sent_id                                                      
t1_fm9xko2 1        [https://giphy.com/gifs/pDsCoECKh1Pa](https://...   
t1_fm9xn5t 1                                    May they rest in hell   
t1_fm9xwr3 1                   Well, well, well, how the turn tables.   
t1_fm9xzo3 1                                                [removed]   
t1_fm9y524 1                                                [removed]   
...                                                               ...   
t1_flqkoxy 5                           Trump is simple a poor leader.   
t1_flqkhgb 1                 He is a narcissist of the highest order.   
           2                         He must be removed from office .   
t1_flqk0lf 1                            Sic semper tyrannis: carcerem   
t1_flqjdf1 1        The only way to cure a teenage bully is to lov...   

                   fake_news_flag  comm_has_flags  fake_regex  
comm_id    sent_id                                             
t1_fm9xko2 1                 None               0       False  
t1_fm9xn5t 1                 None               0       False  
t1_fm9xwr3 1                 None               0       False  
t1_fm9xzo3 1                 None               0       False  
t1_fm9y524 1                 None               0       False  
...                           ...             ...         ...  
t1_flqkoxy 5                 None               0       False  
t1_flqkhgb 1                 None               0       False  
           2                 None               0       False  
t1_flqk0lf 1                 None               0       False  
t1_flqjdf1 1                 None               0       False  

[784581 rows x 4 columns]

### Comments not caught by the algo

In [ ]:
'is this website trustworthy?',
'misleading headline, thats not what he meant.',
'nice example of propaganda there',
'look this is extremely misleading',
'you call it wrongly attributed, i call it fake news',
'this is a propaganda article spewing more bs from beijing.',
'this sub is obviously propaganda',
'this sub looks like total propaganda trash',
'sorry this title is a bit misleading...',
"the title is misleading, it's talking about the government in general",
"the title of the article is sensationalized or misleading",
"clickbait title + paywall &#x200b; all it's missing the ads",
"that has to be one of the worst, most misleading headlines of any article on here.",
"completely nonsensical and misleading headline"

In [146]:
for row in sent_df.itertuples():
    if row.fake_regex and row.fake_news_flag is None:
        highlight_re(row.sent, fake_regex_pos)
        print(row.fake_news_flag)
        print('\n')

None




None




None




None




None




...

None




None




None




None




None




In [117]:
sent_df_bs = sent_df[sent_df['comm_has_flags']>0]
sent_df_bs['fake_news_flag']=sent_df_bs['fake_news_flag'].fillna('')
sent_df_bs = sent_df_bs[sent_df_bs['fake_news_flag'].str.lower().str.contains('bs|bullshit')]
for s,sent in zip(sent_df_bs.fake_news_flag, sent_df_bs.sent):
    print('%20s | %50s' % (s,sent))

      it 's bullshit |               Either way it's completely bullshit.
          This is BS |                                        This is BS.
            bullshit |          More bullshit from this Gov’t BS factory.
                  BS |                                            Such BS
            bullshit |                      Trump showboat fake bullshit.
            bullshit |                                       Oh bullshit!
            Bullshit |                                          Bullshit.
    This is bullshit |                             This is pure bullshit.
    this is bullshit |               Why do I feel like this is bullshit.
            bullshit |                                   Such bullshit...
            Bullshit |                                          Bullshit.
headline is bullshit | So he didn't actually get Spanish Flu, this headline is bullshit
            bullshit |                                  Fucking bullshit.
            bullshit |  

In [99]:
sent_df_bs.fake_news_flag.str.lower().value_counts()

bullshit                        208
this is bullshit                 76
bs                               41
this is bs                       24
it 's bullshit                   17
bullshit article                  9
sounds like bullshit              4
bullshit title                    4
article is bullshit               3
it was bullshit                   3
bullshit headline                 3
it was bs                         3
headline is bullshit              3
it 's bs                          3
article is bs                     2
this was bs                       2
this is bullshit article          2
it is bs                          2
stop bullshit                     2
headline is bs                    2
this was bullshit                 1
smell bs                          1
make bullshit                     1
it seems like bs                  1
this is bullshit news             1
this is like bullshit             1
this sounds bs                    1
smells like bs              

In [109]:
sent_df[~sent_df.fake_news_flag.isna()].fake_news_flag.str.lower().value_counts()[:50]

bullshit                       208
fake news                      170
propaganda                      91
this is bullshit                76
title is misleading             73
misleading title                60
bs                              41
this is misleading              37
clickbait                       32
this is propaganda              27
this is fake news               26
this is bs                      24
headline is misleading          24
misleading headline             22
it 's bullshit                  17
misinformation                  15
clickbait title                  9
it is misleading                 9
bullshit article                 9
it 's misleading                 9
this is misinformation           8
this is clickbait                8
it 's fake news                  7
article is misleading            7
it 's propaganda                 7
misleading article               7
this is misleading title         6
disinformation                   5
spreading propaganda